# Data Preprocessing

## Setup

In [1]:
# Importing packages
import numpy as np
import pandas as pd
import os
import seaborn as sns
from datetime import datetime
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LinearRegression, Lasso, Ridge, ElasticNet
from sklearn.metrics import mean_squared_error, r2_score, mean_absolute_error
import matplotlib as plt
import seaborn as sns
import statsmodels.api as sm
from plotnine import ggplot, aes, geom_point
from sklearn.tree import DecisionTreeClassifier
from sklearn.preprocessing import LabelEncoder


In [2]:
# Reading in data

## Reading in DECO data
deco = pd.read_excel("./DECO_v.1.0.xlsx")

## Reading in world indicators data
ind = pd.read_excel("./World Bank Development Indicators.xlsx")

## Reading in country abbreviations
abbr = pd.read_excel("./Country Abbreviations.xlsx")

## Display all columns
pd.set_option('display.max_columns', None)

## Preprocessing

### Creating dummy variables and one-hot encoding

#### Creating dummy variables for strictly categorical variables

In [3]:
# creating categorical dummies

## country
country_dummies = pd.get_dummies(deco["country"]) 

## region
region_dummies = pd.get_dummies(deco["region"]) 

## electoral violence side a
electoral_side_a_dummies = pd.get_dummies(deco["electoral_side_a"]) 

## electoral violence side b
electoral_side_b_dummies = pd.get_dummies(deco["electoral_side_b"]) 

## electoral uncertainty dummy (numeric: 0=low, 1=some, 2=high)
electoral_uncertainty_dummies = pd.get_dummies(deco["electoral_vio_uncertainty"]).rename(columns = {0: 'electoral_vio_uncertainty_0', 1: 'electoral_vio_uncertainty_1', 2:'electoral_vio_uncertainty_2'}, inplace = False) 

## type of violence (numeric: 1=state-based conflict, 2=non-state conflict, 3=one-sided violence, 4=violence in civilian protestsand miscellaneous incident)
type_violence_dummies = pd.get_dummies(deco["type_of_violence"]).rename(columns = {1: 'type_of_violence_1', 2: 'type_of_violence_2', 3:'type_of_violence_3', 4:'type_of_violence_4'}, inplace = False)  

## violent perpetrators (numeric: 1=side a, 2=side b, 3=symmetric, 4=unclear)
electoral_perpetrator_dummies = pd.get_dummies(deco["electoral_perpetrator"]).rename(columns = {1: 'electoral_perpetrator_1', 2: 'electoral_perpetrator_2', 3:'electoral_perpetrator_3', 4:'electoral_perpetrator_4'}, inplace = False)  

## electoral side a 
electoral_side_a_dummies = pd.get_dummies(deco["electoral_side_a"]).rename(columns = {"Public Officials": "side_a_PublicOfficials", "Security forces": "side_a_SecurityForces", "Political supporters": "side_a_PoliticalSupporters", "Unclear": "side_a_Unclear", "Rebel group": "side_a_RebelGroup", "Politicians": "side_a_Politicians", "Milita": "side_a_Militia", "Other": "side_a_Other", "Civilians": "side_a_Civilians", "External actors": "side_a_ExternActors"})

## electoral side b dummies
electoral_side_b_dummies = pd.get_dummies(deco["electoral_side_b"]).rename(columns = {"Political supporters": "side_b_PoliticalSupporters", "Rebel group": "side_b_RebelGroup", "Unclear": "side_b_Unclear", "Civilians": "side_b_Civilians", "Other": "side_b_Other", "Milita": "side_b_Militia", "Politicians": "side_b_Politicians", "Security forces": "side_b_SecurityForces", "Public officials": "side_b_PublicOfficials"})


# concatenating dummy variables to new data frame (deco_clean)
deco_clean = pd.concat([deco, 
                        country_dummies, 
                        region_dummies,
                        electoral_uncertainty_dummies,
                        type_violence_dummies,
                        electoral_perpetrator_dummies,
                        electoral_side_a_dummies,
                        electoral_side_b_dummies
                       ], axis=1)

#### Creating dummy vairables for categories where values can take on more than 1 attribute at a time (e.g. item1;item2...)

In [4]:
# Defining function to parse and one-hot encode categorical variables with >1 attribute

def dummy_multiple_attr(df, column, delimter):
    '''splitting data by delimeter'''
    split_data = df[column].str.split(delimter).explode()
    '''creating list of unique values for input column'''
    data_list = list(split_data[~split_data.str.contains(delimter)].unique())
    '''cleaning and stripping each item in list'''
    data_list = [i.lstrip() for i in data_list]
    '''removing excess punction'''
    #data_list.remove(".")
    '''for loop: interating through each unique value and one-hot encoding column for each item'''
    for i in data_list:
        df[f'{column}_{i}'] = np.where(df[column].str.lower().str.contains(str(i)), 1, 0)


In [5]:
# electoral purposes
dummy_multiple_attr(deco_clean, 'electoral_purpose', ";")

In [6]:
# electoral targets
dummy_multiple_attr(deco_clean, 'electoral_targets', ";")

In [7]:
# electoral type
dummy_multiple_attr(deco_clean, 'electoral_type', ";")

In [8]:
# electoral timing
dummy_multiple_attr(deco_clean, 'electoral_timing', ";")

In [9]:
# Consolidating electoral purpose columns


deco_clean['electoral_purpose_secure elections'] = np.where(((deco_clean['electoral_purpose_secure election']==1)|
                                                            (deco_clean['electoral_purpose_Secure elections']==1)|
                                                           (deco_clean['electoral_purpose_secure elections']==1)), 1 ,0)

deco_clean['electoral_purpose_crack down on protest and/or riot'] = np.where(((deco_clean['electoral_purpose_crack down on prostest and/or riot']==1)|
                                                                            (deco_clean['electoral_purpose_crack down on protest and/or riot']==1) |
                                                                             (deco_clean['electoral_purpose_crack down on protest and/or riot/retaliate violent events']==1)|
                                                                             (deco_clean['electoral_purpose_crack down on riot and/or protest']==1)|
                                                                             (deco_clean['electoral_purpose_crack down on riots and/or protests']==1)|
                                                                             (deco_clean['electoral_purpose_crackdown on protest and/or riot']==1)), 1, 0)

deco_clean['electoral_purpose_divergent affiliations'] = np.where(((deco_clean['electoral_purpose_divergent affiliations']==1)|
                                                                  deco_clean['electoral_purpose_diverging affiliations']==1), 1, 0)

deco_clean['electoral_purpose_unclear'] = np.where(((deco_clean['electoral_purpose_unclear']==1)|
                                                  (deco_clean['electoral_purpose_Unclear']==1)), 1, 0)

deco_clean.drop(columns=['electoral_purpose_secure election','electoral_purpose_Secure elections','electoral_purpose_crack down on prostest and/or riot','electoral_purpose_crack down on protest and/or riot/retaliate violent events','electoral_purpose_crack down on riot and/or protest','electoral_purpose_crack down on riots and/or protests','electoral_purpose_crackdown on protest and/or riot','electoral_purpose_diverging affiliations',])
# drop 'electoral_purpose_secure election', 'electoral_purpose_Secure elections', 

id  type_of_violence  conflict_new_id  \
0         95                 1              230   
1         96                 1              230   
2        175                 2             5036   
3        265                 1              230   
4        266                 1              230   
...      ...               ...              ...   
4228  253925                 3              469   
4229  253926                 4            13998   
4230  253927                 3              469   
4231  253928                 3              469   
4232  256920                 3              469   

                                          conflict_name  dyad_new_id  \
0                        Yemen (North Yemen):Government        10855   
1                        Yemen (North Yemen):Government        10855   
2     Supporters of General Peoples Congress - Suppo...         5646   
3                        Yemen (North Yemen):Government        10855   
4                        Yemen (North Yemen):Government        10855   
...                                                 ...          ...   
4228                    Government of Kenya - Civilians          936   
4229        Government of Kenya - Opponents of Kenyatta        15173   
4230                    Government of Kenya - Civilians          936   
4231                    Government of Kenya - Civilians          936   
4232                    Government of Kenya - Civilians          936   

      side_a_new_id                                  side_a  side_b_new_id  \
0               123       Government of Yemen (North Yemen)           1091   
1               123       Government of Yemen (North Yemen)           1091   
2              3425  Supporters of General Peoples Congress           2374   
3               123       Government of Yemen (North Yemen)           1091   
4               123       Government of Yemen (North Yemen)           1091   
...             ...                                     ...            ...   
4228             91                     Government of Kenya              1   
4229             91                     Government of Kenya           6777   
4230             91                     Government of Kenya              1   
4231             91                     Government of Kenya              1   
4232             91                     Government of Kenya              1   

                         side_b  country_id              country       region  \
0                    Ansarallah         678  Yemen (North Yemen)  Middle East   
1                    Ansarallah         678  Yemen (North Yemen)  Middle East   
2     Supporters of Islah party         678  Yemen (North Yemen)  Middle East   
3                    Ansarallah         678  Yemen (North Yemen)  Middle East   
4                    Ansarallah         678  Yemen (North Yemen)  Middle East   
...                         ...         ...                  ...          ...   
4228                  Civilians         501                Kenya       Africa   
4229      Opponents of Kenyatta         501                Kenya       Africa   
4230                  Civilians         501                Kenya       Africa   
4231                  Civilians         501                Kenya       Africa   
4232                  Civilians         501                Kenya       Africa   

                                         source_article  year date_start  \
0     Agence France Presse, 2012-02-21, Four killed ...  2012 2012-02-21   
1     Agence France Presse, 2012-02-21, Four killed ...  2012 2012-02-21   
2     Reuters 1997-04-21 "Yemeni man killed in pre-e...  1997 1997-04-20   
3     Agence France Presse, 2012-02-09, Two killed i...  2012 2012-02-09   
4     Rueters News, 2012-02-20,WRAPUP 3-Violence hit...  2012 2012-02-20   
...                                                 ...   ...        ...   
4228  "Human Rights Watch,2018-02-25,Kenya: Fresh Ev...  2017 2017-10-31   
4229  "Human R

### Missing values

In [10]:
# Checking for missing values
missing_values_count = deco_clean.isnull().sum() # generating array of missing values and columns
pd.set_option('display.max_rows', None) # setting view to all rows
pd.DataFrame(missing_values_count).reset_index().rename(columns={"index":"column",0:"n"}).sort_values(by="n", ascending=False) # data

column     n
33                                  electoral_side_b_2  4231
30                                  electoral_side_a_2  3974
27                                electoral_vio_source  3261
12                                      source_article     9
23                                            latitude     3
24                                           longitude     3
29                                    electoral_side_a     1
141                         side_a_PoliticalSupporters     0
142                                 side_a_Politicians     0
143                                   Public officials     0
144                                  side_a_RebelGroup     0
150                         side_b_PoliticalSupporters     0
145                              side_a_SecurityForces     0
146                                     side_a_Unclear     0
147                                   side_b_Civilians     0
148                                     side_b_Militia     0
149                                       side_b_Other     0
151                                 side_b_Politicians     0
152                             side_b_PublicOfficials     0
153                                  side_b_RebelGroup     0
154                              side_b_SecurityForces     0
155                                     side_b_Unclear     0
156                          electoral_purpose_disrupt     0
157           electoral_purpose_divergent affiliations     0
158  electoral_purpose_crack down on protest and/or...     0
159                  electoral_purpose_protect results     0
160                          electoral_purpose_unclear     0
161                            electoral_purpose_spell     0
162               electoral_purpose_eliminate opponent     0
163           electoral_purpose_retaliate violent acts     0
164                 electoral_purpose_overturn results     0
140                                       side_a_Other     0
0                                                   id     0
139                                     side_a_Militia     0
126                        electoral_vio_uncertainty_0     0
115                                            Ukraine     0
116                                     United Kingdom     0
117                                          Venezuela     0
118                                Yemen (North Yemen)     0
119                                             Zambia     0
120                                Zimbabwe (Rhodesia)     0
121                                             Africa     0
122                                           Americas     0
123                                               Asia     0
124                                             Europe     0
125                                        Middle East     0
127                        electoral_vio_uncertainty_1     0
138                                side_a_ExternActors     0
128                        electoral_vio_uncertainty_2     0
129                                 type_of_violence_1     0
130                                 type_of_violence_2     0
131                                 type_of_violence_3     0
132                                 type_of_violence_4     0
133                            electoral_perpetrator_1     0
134                            electoral_perpetrator_2     0
135                            electoral_perpetrator_3     0
136                            electoral_perpetrator_4     0
137                                   side_a_Civilians     0
166              electoral_purpose_preemptive violence     0
165                 electoral_purpose_secure elections     0
170               electoral_purpose_repress opposition     0
167              electoral_purpose_prevent from voting     0
168                    electoral_purpose_shape results     0
195                                electoral_targets_6     0
196                                electoral_targets_3     0
197                   

In [11]:
# Filling in missing values

## filling in NAs for electoral_side_a
deco_clean['electoral_side_a'] = deco_clean['electoral_side_a'].fillna("Unclear")

## filling in NAs for longitude and latitude
deco_clean['longitude'] = deco_clean['longitude'].fillna(-99)
deco_clean['latitude'] = deco_clean['latitude'].fillna(-99)

## filling in NAs for electoral_vio_source
deco_clean['electoral_vio_source'] = deco_clean['electoral_vio_source'].fillna("None/Unknown")

## filling in NAs for source article
deco_clean['source_article'] = deco_clean['source_article'].fillna("None/Unknown")


### Merging DECO data with indicators

In [12]:
# Creating country-year identifier for indicators
ind['country_year'] = ind['Country Abbreviation'] + ind['Year']
ind.head()


Country  Year Country Abbreviation  GDP (constant 2015 US$)  \
0  Afghanistan  1985                  AFG                      0.0   
1  Afghanistan  1986                  AFG                      0.0   
2  Afghanistan  1987                  AFG                      0.0   
3  Afghanistan  1988                  AFG                      0.0   
4  Afghanistan  1989                  AFG                      0.0   

   GDP growth (annual %)  GDP per capita (constant 2015 US$)  Gini index  \
0                    0.0                                 0.0         0.0   
1                    0.0                                 0.0         0.0   
2                    0.0                                 0.0         0.0   
3                    0.0                                 0.0         0.0   
4                    0.0                                 0.0         0.0   

   Inflation, consumer prices (annual %)  \
0                                    0.0   
1                                    0.0   
2                                    0.0   
3                                    0.0   
4                                    0.0   

   Political Stability and Absence of Violence/Terrorism: Estimate  \
0                                                0.0                 
1                                                0.0                 
2                                                0.0                 
3                                                0.0                 
4                                                0.0                 

   Unemployment, total (% of total labor force) (modeled ILO estimate)  \
0                                                0.0                     
1                                                0.0                     
2                                                0.0                     
3                                                0.0                     
4                                                0.0                     

  country_year  
0      AFG1985  
1      AFG1986  
2      AFG1987  
3      AFG1988  
4      AFG1989

In [13]:
# List of countries in DECO data
list(deco_clean['country'].unique())

['Yemen (North Yemen)',
 'Algeria',
 'Egypt',
 'Sudan',
 'Burundi',
 'Cambodia (Kampuchea)',
 'Benin',
 'Madagascar (Malagasy)',
 'Lesotho',
 'Djibouti',
 'Guinea',
 'Ghana',
 'Gambia',
 'Malawi',
 'Mali',
 'Nigeria',
 'South Africa',
 'Mozambique',
 'Namibia',
 'Tanzania',
 'Angola',
 'Zimbabwe (Rhodesia)',
 'DR Congo (Zaire)',
 'Guinea-Bissau',
 'Somalia',
 'Papua New Guinea',
 'Central African Republic',
 'Uganda',
 'Sierra Leone',
 'Ivory Coast',
 'Ethiopia',
 'Senegal',
 'Mauritania',
 'Libya',
 'Kenya',
 'Congo',
 'Philippines',
 'Iraq',
 'Myanmar (Burma)',
 'Pakistan',
 'Thailand',
 'India',
 'Spain',
 'United Kingdom',
 'Albania',
 'Honduras',
 'Ecuador',
 'Venezuela',
 'Brazil',
 'Indonesia',
 'Mexico',
 'Fiji',
 'Bangladesh',
 'Sri Lanka',
 'Nepal',
 'Jamaica',
 'Italy',
 'Kyrgyzstan',
 'Dominican Republic',
 'Bolivia',
 'Iran',
 'Colombia',
 'El Salvador',
 'Afghanistan',
 'Turkey',
 'Nicaragua',
 'Peru',
 'Tunisia',
 'Ukraine',
 'Kosovo',
 'Israel',
 'Moldova',
 'Lebanon',


In [14]:
ind['Country Abbreviation'].unique()

array(['AFG', 'ALB', 'DZA', 'ASM', 'AND', 'AGO', 'ATG', 'ARG', 'ARM',
       'ABW', 'AUS', 'AUT', 'AZE', 'BHS', 'BHR', 'BGD', 'BRB', 'BLR',
       'BEL', 'BLZ', 'BEN', 'BMU', 'BTN', 'BOL', 'BIH', 'BWA', 'BRA',
       'VGB', 'BRN', 'BGR', 'BFA', 'BDI', 'CPV', 'KHM', 'CMR', 'CAN',
       'CYM', 'CAF', 'TCD', 'CHL', 'CHN', 'COL', 'COM', 'COD', 'COG',
       'CRI', 'CIV', 'HRV', 'CUB', 'CUW', 'CYP', 'CZE', 'DNK', 'DJI',
       'DMA', 'DOM', 'ECU', 'EGY', 'SLV', 'GNQ', 'ERI', 'EST', 'SWZ',
       'ETH', 'FRO', 'FJI', 'FIN', 'FRA', 'PYF', 'GAB', 'GMB', 'GEO',
       'DEU', 'GHA', 'GIB', 'GRC', 'GRL', 'GRD', 'GUM', 'GTM', 'GIN',
       'GNB', 'GUY', 'HTI', 'HND', 'HKG', 'HUN', 'ISL', 'IND', 'IDN',
       'IRN', 'IRQ', 'IRL', 'IMN', 'ISR', 'ITA', 'JAM', 'JPN', 'JOR',
       'KAZ', 'KEN', 'KIR', 'PRK', 'KOR', 'XKK', 'KWT', 'KGZ', 'LAO',
       'LVA', 'LBN', 'LSO', 'LBR', 'LBY', 'LIE', 'LTU', 'LUX', 'MAC',
       'MDG', 'MWI', 'MYS', 'MDV', 'MLI', 'MLT', 'MHL', 'MRT', 'MUS',
       'MEX', 'FSM',

In [15]:
# Cleaning countries so that they can match abbreviations data
deco_clean['country_new'] = np.where(deco_clean['country']=="Yemen (North Yemen)", "Yemen", 
                                np.where(deco_clean['country']=="Cambodia (Kampuchea)", "Cambodia",
                                        np.where(deco_clean['country']== 'Madagascar (Malagasy)', "Madagascar",
                                                np.where(deco_clean['country']=="Zimbabwe (Rhodesia)", "Zimbabwe",
                                                        np.where(deco_clean['country']=='DR Congo (Zaire)', "DR Congo",
                                                                np.where(deco_clean['country']=='Myanmar (Burma)', "Myanmar",
                                                                        np.where(deco_clean['country']=='Russia (Soviet Union)', "Russia",
                                                                                np.where(deco_clean['country']=='Serbia (Yugoslavia)', "Serbia", deco_clean['country']))))))))

In [16]:
# Merging country abbreviations onto DECO data
deco_clean= pd.merge(deco_clean, abbr, left_on='country_new', right_on="Country", how="left")

In [17]:
# Creating country-year identifier
deco_clean['year_string'] = deco_clean['year'].apply(lambda x: str(x))
deco_clean['country_year'] = deco_clean['Abbreviation'] + deco_clean['year_string']
deco_clean.head(100)

id  type_of_violence  conflict_new_id  \
0     95                 1              230   
1     96                 1              230   
2    175                 2             5036   
3    265                 1              230   
4    266                 1              230   
5    280                 2             5036   
6    307                 2             5036   
7    339                 1              230   
8    343                 1            11148   
9    344                 2             5036   
10   399                 2             5036   
11   403                 2             5037   
12   490                 1              230   
13   528                 1              230   
14   534                 1              230   
15   535                 1              230   
16   537                 3              715   
17   707                 2             5036   
18   868                 1            11148   
19  1089                 1              169   
20  1117                 1              169   
21  1124                 1              169   
22  1205                 1              169   
23  1206                 2              169   
24  1221                 2              169   
25  1223                 3             4428   
26  1224                 1              169   
27  1236                 2              169   
28  1260                 2              169   
29  1268                 2              169   
30  1338                 1              169   
31  1343                 2              169   
32  1675                 3              706   
33  2058                 3             4262   
34  2085                 3             4262   
35  2300                 4            14005   
36  2408                 3              706   
37  2574                 3              572   
38  2581                 4            14005   
39  2586                 1              386   
40  2587                 1              386   
41  2593                 4            14005   
42  2715                 1              386   
43  2735                 1              386   
44  2783                 1              386   
45  2790                 3              572   
46  2839                 4            14005   
47  2883                 1              386   
48  2950                 4            14005   
49  2989                 4            14005   
50  3082                 3              572   
51  3160                 1              386   
52  3211                 3              572   
53  3650                 1              386   
54  3698                 3              572   
55  3733                 1              386   
56  3877                 1              386   
57  3922                 1              386   
58  4005                 1              386   
59  4114                 1              386   
60  4127                 4            14005   
61  4136                 3              573   
62  4162                 1              386   
63  4201                 1              386   
64  4216                 1              386   
65  4290                 1              386   
66  4347                 4            14005   
67  4429                 3              572   
68  4483                 4            14005   
69  4687                 1              386   
70  4777                 4            14005   
71  4780                 4            14005   
72  4781                 4            14005   
73  4784                 4            14005   
74  4838                 3              572   
75  4848                 3              572   
76  4953                 4            14005   
77  4962                 1              386   
78  5040                 3             1034   
79  5079                 1              386   
80  5080                 1              386   
81  5114                 1              386   
82  5129                 1              386   
83  5165                 1              386   
84  5215   

In [18]:
# Merging indicators with DECO data on country-year identifier
deco_clean = pd.merge(deco_clean, ind, on='country_year', how="left")
deco_clean.head(200)

id  type_of_violence  conflict_new_id  \
0       95                 1              230   
1       96                 1              230   
2      175                 2             5036   
3      265                 1              230   
4      266                 1              230   
5      280                 2             5036   
6      307                 2             5036   
7      339                 1              230   
8      343                 1            11148   
9      344                 2             5036   
10     399                 2             5036   
11     403                 2             5037   
12     490                 1              230   
13     528                 1              230   
14     534                 1              230   
15     535                 1              230   
16     537                 3              715   
17     707                 2             5036   
18     868                 1            11148   
19    1089                 1              169   
20    1117                 1              169   
21    1124                 1              169   
22    1205                 1              169   
23    1206                 2              169   
24    1221                 2              169   
25    1223                 3             4428   
26    1224                 1              169   
27    1236                 2              169   
28    1260                 2              169   
29    1268                 2              169   
30    1338                 1              169   
31    1343                 2              169   
32    1675                 3              706   
33    2058                 3             4262   
34    2085                 3             4262   
35    2300                 4            14005   
36    2408                 3              706   
37    2574                 3              572   
38    2581                 4            14005   
39    2586                 1              386   
40    2587                 1              386   
41    2593                 4            14005   
42    2715                 1              386   
43    2735                 1              386   
44    2783                 1              386   
45    2790                 3              572   
46    2839                 4            14005   
47    2883                 1              386   
48    2950                 4            14005   
49    2989                 4            14005   
50    3082                 3              572   
51    3160                 1              386   
52    3211                 3              572   
53    3650                 1              386   
54    3698                 3              572   
55    3733                 1              386   
56    3877                 1              386   
57    3922                 1              386   
58    4005                 1              386   
59    4114                 1              386   
60    4127                 4            14005   
61    4136                 3              573   
62    4162                 1              386   
63    4201                 1              386   
64    4216                 1              386   
65    4290                 1              386   
66    4347                 4            14005   
67    4429                 3              572   
68    4483                 4            14005   
69    4687                 1              386   
70    4777                 4            14005   
71    4780                 4            14005   
72    4781                 4            14005   
73    4784                 4            14005   
74    4838                 3              572   
75    4848                 3              572   
76    4953                 4            14005   
77    4962                 1              386   
78    5040                 3             1034   
79    5079                 1              386   
80    5080                 1           

### Final cleaning and preprocessing before model 

In [20]:
# Dropping obsolete variables
deco_clean_final = deco_clean.drop(columns = ['id',
                                              'conflict_name', # already label encoded as "conflict_new_id"
                                              'type_of_violence', # already one hot encoded
                                              'side_a', # already label encoded as "side_a_new_id"
                                              'side_b', # already label encoded as "side_b_new_id"
                                              'country', # already one-hot encoded and label encoded as "country_id"
                                              'region', # already one-hot encoded 
                                              'source_article', # dropping
                                              'electoral_vio_source', # dropping
                                              'electoral_purpose', # already one-hot encoded
                                              'electoral_side_a', # already one-hot encoded
                                              'electoral_side_a_2', # dropping
                                              'electoral_side_b', # already one-hot encoded
                                              'electoral_side_b_2', # dropping
                                              'country_id', # countries already one hot encoded
                                              'relid', # dropping
                                              'longitude',
                                              'latitude',
                                              'date_start',
                                              'date_end',
                                              'electoral_purpose_.',
                                              'country_new',
                                              'Country_x',
                                              'Country_y',
                                              'Abbreviation',
                                              'year_string',
                                              'country_year',
                                              'Country Abbreviation',
                                              'country_year',
                                              "Year"
                                    
                                              
                                    ])
# Exporting CSV
deco_clean.to_csv('deco_clean.csv', index=False) # for exploratory data analysis
deco_clean_final.to_csv('deco_clean_final.csv', index=False) # for ML 